In [3]:
import param as pm
import panel as pn

In [32]:
# Add the Vega extension for Panel
pn.extension('vega')

# Add an external CSS file to make it look nicer!
pn.extension(css_files=["https://codepen.io/chriddyp/pen/bWLwgP.css"])

In [4]:
from geopandas import gpd

In [5]:
import osmnx as ox

In [81]:
lat_min, lng_min, lat_max, lng_max = [40.722889737951824,-74.00590350678908,40.762947752755395,-73.97174289277541]

In [ ]:
[-74.00590350678908,40.722889737951824]
1: [-73.97174289277541,40.722889737951824]
2: [-73.97174289277541,40.762947752755395]
3: [-74.00590350678908,40.762947752755395]

In [24]:
G = ox.graph_from_address("Times square, New York", 
                          distance=2000,network_type='drive')

In [25]:
ox.extended_stats(G).keys()

dict_keys(['avg_neighbor_degree', 'avg_neighbor_degree_avg', 'avg_weighted_neighbor_degree', 'avg_weighted_neighbor_degree_avg', 'degree_centrality', 'degree_centrality_avg', 'clustering_coefficient', 'clustering_coefficient_avg', 'clustering_coefficient_weighted', 'clustering_coefficient_weighted_avg', 'pagerank', 'pagerank_max_node', 'pagerank_max', 'pagerank_min_node', 'pagerank_min'])

In [11]:
import networkx as nx

In [12]:
import folium

In [13]:
from IPython.display import IFrame # loads HTML files

In [14]:
import io

In [44]:
html = io.StringIO()
route_graph_map.save(html)

TypeError: string argument expected, got 'bytes'

In [45]:
figure = folium.Figure(width=450, height=450)
route_graph_map.add_to(figure)
#figure.get_root().render()

'<!DOCTYPE html>\n<head>    \n    <meta http-equiv="content-type" content="text/html; charset=UTF-8" />\n    \n        <script>\n            L_NO_TOUCH = false;\n            L_DISABLE_3D = false;\n        </script>\n    \n    <script src="https://cdn.jsdelivr.net/npm/leaflet@1.5.1/dist/leaflet.js"></script>\n    <script src="https://code.jquery.com/jquery-1.12.4.min.js"></script>\n    <script src="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/js/bootstrap.min.js"></script>\n    <script src="https://cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js"></script>\n    <link rel="stylesheet" href="https://cdn.jsdelivr.net/npm/leaflet@1.5.1/dist/leaflet.css"/>\n    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap.min.css"/>\n    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css"/>\n    <link rel="stylesheet" href="https://maxcdn.bootstrapcdn.com/font-awesome

In [ ]:
#figure.get_root().render()

In [39]:
import base64
def folium_to_iframe(chart, width,height):
    import io
    import base64

    figure = folium.Figure(width=width, height=height)
    chart.add_to(figure)
    html = figure.get_root().render()

    iframe = """
    <iframe width="{width}" height="{height}" src="{html}"
    frameborder="0" scrolling="no" marginheight="0" marginwidth="0"></iframe>
    """.format(
        width=width, height=height, html=html
    )

    return iframe

In [41]:
origin = gpd.tools.geocode("Times square", provider='nominatim', user_agent="my-application")
destination = gpd.tools.geocode("Empire state building", provider='nominatim', user_agent="my-application")

In [138]:
destination.geometry.y

0    40.757281
dtype: float64

In [148]:
from matplotlib import pyplot as plt
import tkinter
import matplotlib
matplotlib.use('TkAgg')

In [61]:
class RoutePlanning(pm.Parameterized): 
    From = pm.String(default="Times square", doc = "Your origin.")
    To = pm.String(default="Empire state building", doc = "Your destination.")
    
    @pm.depends('From', 'To', watch=True)
    def _update_(self):
        new_From = self.From
        new_To = self.To
        self.From = new_From
        self.To = new_To
        
        
    @pm.depends('From','To')
    def heatmap(self):
        """
        Return a Folium map with a heatmap showing the currently 
        selected data.
        """
        # initialize the Folium map
        origin = gpd.tools.geocode(self.From, provider='nominatim', user_agent="my-application")
        destination = gpd.tools.geocode(self.To, provider='nominatim', user_agent="my-application")
        
        start = list(zip(origin.geometry.y, origin.geometry.x))
        end = list(zip(destination.geometry.y, destination.geometry.x))
        
        orig_node = ox.get_nearest_node(G, start[0]) 
        dest_node = ox.get_nearest_node(G, end[0])
        
        route = nx.shortest_path(G, 
                         orig_node, dest_node, 
                         weight='length')
        
        # The interactive map of the street network
        graph_map = ox.plot_graph_folium(G, popup_attribute="name", edge_width=2)

        # The interactive map of the route, with the streets in the background
        route_graph_map = ox.plot_route_folium(G, route, route_map=graph_map)
       
        
        filepath = 'foliumChart.html'
        route_graph_map.save(filepath)
        figure = folium.Figure(width=450, height=450)
        route_graph_map.add_to(figure)

        # return the Pane object
        return IFrame(filepath, width=600, height=500)#pn.pane.HTML(folium_to_iframe(route_graph_map, width=600, height=500))

In [62]:
app = RoutePlanning(name="")

In [63]:
# Layout the panel
panel = pn.Column(
    #pn.Row(pn.Column(title, app.summary_text), app.param),
    pn.Row(pn.Param(app.param,widgets={'From':pn.widgets.TextInput,'To':pn.widgets.TextInput})),
    pn.Row(app.heatmap)
)

In [64]:
app.heatmap()

In [65]:
panel.servable()

Column
    [0] Row
        [0] Param(RoutePlanning, widgets={'From': <class 'panel.wid...})
    [1] Row
        [0] ParamMethod(method)